<hr size=7 color=#8D84B5 > </hr> 

<div align="center">

# <font color = #6b4cde face="Verdana"> **Universities and Gentrification**
## <font color = #6b4cde face="Verdana"> **UMD CMSC320 Data Science, Spring 2023** </font>
## <font color = #6b4cde face="Verdana"> **Joe Diaz and Connor Pymm** </font>
</center>

</div>

<hr size=7 color=#8D84B5 > </hr> 

### 🙏RUN ME FIRST🙏

In [44]:
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots

import numpy as np
import statsmodels.api as sm
import statsmodels.formula.api as smf

<hr size=7 color=#8D84B5 > </hr> 

<div align="center">

## <font color = #6b4cde face="Verdana"> **Data Curation** </font>
</center>

</div>

<hr size=7 color=#8D84B5 > </hr> 

### Selecting Datasets

In order to perform analysis on colleges and their surrounding regions, we needed to
find some subset of colleges, a dataset with characteristics of those colleges on a yearly basis, 
and then a dataset with characteristics of their nearby geographical areas. again yearly. 

Initially, we decided to limit our analysis to the top 100 universities in the country 
according to current US News rankings, under the assumption that more highly ranked universities 
might have a more significant impact on their respective communities. We used Andy Reiter's
“U.S. News & World Report Historical Liberal Arts College and University Rankings” dataset (**citation**).
  
In order to obtain college characteristics, we discovered that the Department of
Education has extensive data available on accredited universities called the College Scorecard, which has
a public API for programatically querying data.
  
In order to obtain characteristics of the region around each university, we needed a dataset that would contain
demographic and economic data for defined geographical regions associated with the location of the University.
We found that the American Community Survey yearly data from the Census had the housing cost and income data we
wanted to analyze, and that its Public Use Microdata API from the census allowed us to programatically request that
data for geographical groupings called "Public Use Microdata Areas," which are the smallest geographical entities that
the Census collects yearly data from.

### Extract, Transform, and Load

Since we queried a *substantial* amount of data from *ridiculously large* datasets,
and requesting federal data from the Department of Education and the Census required
registration for and usage of API keys, we decided that on top of the source datasets that
we were able to download in full, stored in our repository under ETL/source_data, we would
create modules for making federal API requests and loading the results into csv files for usage
later. 
  
Dataframes that we generated from data that we queried were stored under ETL/generated_data
as csv, and then loaded into the notebook when needed, specifically: we built ScorecardData.csv using
our scorecard_client.py module, which defines a CollegeScorecardClient object that can be used to query
DoE data, given a valid API key, set of desired variables, and set of colleges using IPEDS IDs, we built 
college_FIPs by combining the university list we got from Reiter with state FIPs data from DoE and county 
FIPs data by collecting them manually university by university.

For the rest of this tutorial, we will be using the data we collected by default, but if you would like to
recreate the analysis of this tutorial using a different set of colleges, and thus your own datasets, you can
fork this repository and use the modules provided in the ETL/ directory to do so.

<hr size=7 color=#8D84B5 > </hr> 

<div align="center">

## <font color = #6b4cde face="Verdana"> **Data Processing** </font>
</center>

</div>

<hr size=7 color=#8D84B5 > </hr> 

### Loading and Representation

Here, we load the data we have downloaded or generated locally into our
notebook for use to use in our analysis. We stored each of our datasets as
csv, so they are easily loaded into Pandas Dataframes. We will also have to define a few new terms so that the reader can understand what we are talking about:
1. **MSA**: The MSA is the metropolitan statistical area in the U.S. Census. It includes 384 census-designated regions in the U.S. with more than 50,000 people in each block. We use this data as a standard for the general region around colleges and as a sort of control variable compared to our more limited and specific PUMA.
2. **PUMA**: The PUMAs stands for "Public Use Microdata Areas", which is kind of in between a county and a school system in the Census. IT was the smallest readily available geography in the Census dataset that we could convert to using zip codes and tracts, so we use it as our specific locality that we are comparing against our control (MSA). If our hypothesis is correct, these should be more volatile since the prices of colleges should be driving up prices in these localities.
3. **Tract**: A Census Tract is a specific section of land, even more specific than the PUMA, that we use to connect the zip codes from the top 100 universities and the MSAs and PUMA's from the Census. They are very finnicky and hard to work with, but we found a U.S. government API that allows us to convert between Zip Codes, Census Tracts, and MSAs, which allowed us to complete our analysis.
4. **Zip Code**: You likely already know what a zip code is, but working with Zip Codes was a very difficult challenge in this project since they are maintained by the U.S. Postal Service, not the Census, so neither agency has a standard measurement for localities, hence why we needed to convert from Zip -> Tract -> MSA and PUMA.

In [45]:
# Read dataframes from Scorecard generated data
scard_df = pd.read_csv("ETL/generated_data/ScorecardData.csv")
fips_df = pd.read_csv("ETL/generated_data/college_FIPs.csv")
cpi_df = pd.read_csv("ETL/source_data/cpi_all.csv").groupby("Year")["Value"].mean()
scard_df.head()

student.size  cost.tuition.in_state  cost.tuition.out_of_state  \
0        5042.0                    NaN                        NaN   
1       18337.0                    NaN                        NaN   
2       10395.0                    NaN                        NaN   
3        9203.0                    NaN                        NaN   
4       10120.0                    NaN                        NaN   

   cost.avg_net_price.public  cost.avg_net_price.private      id  \
0                        NaN                         NaN  131159   
1                        NaN                         NaN  100858   
2                        NaN                         NaN  223232   
3                        NaN                         NaN  196079   
4                        NaN                         NaN  164924   

             school.name  school.carnegie_size_setting  school.zip  \
0    American University                            17  20016-8001   
1      Auburn University                            15       36849   
2      Baylor University                            16       76798   
3  Binghamton University                            16  13850-6000   
4         Boston College                            17       02467   

   school.region_id  school.state_fips  school.locale  school.ownership  year  
0                 2                 11             11                 2  1996  
1                 5                  1             13                 1  1996  
2                 6                 48             12                 2  1996  
3                 2                 36             22                 1  1996  
4                 1                 25             13                 2  1996

In [46]:
years = range(2009, 2020)
msa_path_format = "ETL/generated_data/MSA{y}.csv"
MSA_frames = [
    pd.read_csv(msa_path_format.format(y=yr)).assign(year=yr)
    for yr in years
]
msa_df = pd.concat(MSA_frames)
msa_df.columns = ["name", "msa_income", "msa_rent", "msa", "year"]
print(msa_df["name"].unique().shape)
msa_df

(36,)


name  msa_income  msa_rent      msa  year
0             CO Metro Area"       59007      1207   19740]  2009
1             NC Metro Area"       49902       921   20500]  2009
2             FL Metro Area"       37654       881   23540]  2009
3             NC Metro Area"       41272       789   24660]  2009
4             SC Metro Area"       43283       763   24860]  2009
..                       ...         ...       ...      ...   ...
56            CA Metro Area"       77774      1774   31080]  2019
57            WI Metro Area"       75545      1218   31540]  2019
58   DC-VA-MD-WV Metro Area"      105659      1862   47900]  2019
59            NC Metro Area"       52322       815   49180]  2019
60         MA-CT Metro Area"       76348      1319  49340]]  2019

[657 rows x 5 columns]

In [47]:
years = range(2009, 2020)
puma_path_format = "ETL/generated_data/PUMA{y}.csv"
PUMA_frames = [
    pd.read_csv(puma_path_format.format(y=yr)).assign(year=yr)
    for yr in years
]
puma_df = pd.concat(PUMA_frames).reset_index(drop=True)
puma_df.columns = ["puma_income", "puma_rent", "state", "puma", "year"]
puma_df["state"] = puma_df["state"].astype("int")
puma_df["puma"] = puma_df["puma"].astype("int")
puma_df["year"] = puma_df["year"].astype("int")

print(puma_df["puma"].unique().shape)
puma_df

(84,)


puma_income  puma_rent  state  puma  year
0           52023       1060      6  1800  2009
1           36740       1020      6  1901  2009
2           69677       1710      6  2001  2009
3           49350       1244      6  2101  2009
4           70522       1561      6  2201  2009
...           ...        ...    ...   ...   ...
3414       101524       1921     51  1302  2019
3415        51987        751     55   100  2019
3416        57284       1254     55   101  2019
3417        61443        767     55  1301  2019
3418        65851        826     55  1600  2019

[3419 rows x 5 columns]

### Data Cleaning and Reshaping

The data that we have still uses the variable names and formatting of our
original sources, and those variable names are unweildy and not ideal for usage
in analysis later, so we rename our columns to be more human readable and
developer friendly. Additionally, cost data in our sources does not account for
inflation, so we should use an all-consumers/all-goods CPI to transform our dollar
values to a standard value.

In [48]:
# Rename columns to be more readable, usable
scard_df = scard_df.rename(
    columns={
        "student.size": "size",
        "cost.tuition.in_state": "in_state_tuition",
        "cost.tuition.out_of_state": "out_state_tuition",
        "cost.avg_net_price.public": "public_net_price",
        "cost.avg_net_price.private": "private_net_price",
        "id": "id",
        "school.name": "name",
        "school.carnegie_size_setting": "size_setting",
        "school.zip": "zip",
        "school.state_fips": "state_fips",
        "school.region_id": "region_id",
        "school.locale": "locale",
        "school.ownership": "ownership"
    }
)

# Join county FIPs codes into College Scorecard dataframe for use later in
# associating with Census geographies.
scard_df = pd.merge(
    scard_df, 
    fips_df[["id", "county", "cbsa", "puma"]], 
    on="id", how="left").drop_duplicates()
print(scard_df)

# Combine public and private net prices into a single net price column, and drop those columns
scard_df["net_cost"] = scard_df.apply(lambda row: 
            row["public_net_price"] if (row["ownership"] == 1) else row["private_net_price"],
        axis=1
)
scard_df["net_cost_adjusted"] = scard_df.apply(lambda row: 
            (row["net_cost"]/cpi_df.at[row["year"]]) * 100,
        axis=1
)
scard_df["in_tuition_adjusted"] = scard_df.apply(lambda row: 
            (row["in_state_tuition"]/cpi_df.at[row["year"]]) * 100,
        axis=1
)
scard_df["out_tuition_adjusted"] = scard_df.apply(lambda row: 
            (row["out_state_tuition"]/cpi_df.at[row["year"]]) * 100,
        axis=1
)
scard_df["non_tuition_expenses_adj"] = scard_df.apply(lambda row: 
            row["net_cost_adjusted"] - row["in_tuition_adjusted"],
        axis=1
)



scard_df["state_fips"] = scard_df["state_fips"].astype(int)
scard_df["year"] = scard_df["year"].astype(int)
scard_df.drop(["public_net_price", "private_net_price"], axis=1, inplace=True)
scard_df.head()

         size  in_state_tuition  out_state_tuition  public_net_price  \
0      5042.0               NaN                NaN               NaN   
1     18337.0               NaN                NaN               NaN   
2     18337.0               NaN                NaN               NaN   
3     10395.0               NaN                NaN               NaN   
4      9203.0               NaN                NaN               NaN   
...       ...               ...                ...               ...   
3820   7366.0           57386.0            57386.0               NaN   
3821   6217.0           23628.0            46854.0           19593.0   
3822   4804.0           54416.0            54416.0               NaN   
3823   4701.0           57700.0            57700.0               NaN   
3824   2619.0           46475.0            46475.0               NaN   

      private_net_price      id                               name  \
0                   NaN  131159                American Universit

size  in_state_tuition  out_state_tuition      id  \
0   5042.0               NaN                NaN  131159   
1  18337.0               NaN                NaN  100858   
2  18337.0               NaN                NaN  100858   
3  10395.0               NaN                NaN  223232   
4   9203.0               NaN                NaN  196079   

                    name  size_setting         zip  region_id  state_fips  \
0    American University            17  20016-8001          2          11   
1      Auburn University            15       36849          5           1   
2      Auburn University            15       36849          5           1   
3      Baylor University            16       76798          6          48   
4  Binghamton University            16  13850-6000          2          36   

   locale  ownership  year  county     cbsa    puma  net_cost  \
0      11          2  1996     1.0  47900.0   101.0       NaN   
1      13          1  1996    81.0  12220.0  2101.0       NaN   
2      13          1  1996    81.0  10760.0  2101.0       NaN   
3      12          2  1996   309.0  47380.0  3801.0       NaN   
4      22          1  1996     7.0  13780.0  2201.0       NaN   

   net_cost_adjusted  in_tuition_adjusted  out_tuition_adjusted  \
0                NaN                  NaN                   NaN   
1                NaN                  NaN                   NaN   
2                NaN                  NaN                   NaN   
3                NaN                  NaN                   NaN   
4                NaN                  NaN                   NaN   

   non_tuition_expenses_adj  
0                       NaN  
1                       NaN  
2                       NaN  
3                       NaN  
4                       NaN

In [49]:
locale_map = {
    11:	"City: Large",
    12:	"City: Midsize",
    13:	"City: Small",
    21:	"Suburb: Large",
    22:	"Suburb: Midsize",
    23:	"Suburb: Small",
    31:	"Town: Fringe",
    32:	"Town: Distant",
    33:	"Town: Remote",
    41:	"Rural: Fringe",
    42:	"Rural: Distant",
    43:	"Rural: Remote"
}
ownership_map = {
    1:	"Public",
    2:	"Private nonprofit",
    3:	"Private for-profit"
}
region_map = {
    0:	"U.S. Service Schools",
    1:	"New England",
    2:	"Mid East",
    3:	"Great Lakes",
    4:	"Plains",
    5:	"Southeast",
    6:	"Southwest",
    7:	"Rocky Mountains",
    8:	"Far West",
    9:	"Outlying Areas"
}

scard_df["region"] = scard_df.apply(lambda row: 
            region_map[row["region_id"]],
        axis=1
)
scard_df["ownership"] = scard_df.apply(lambda row: 
            ownership_map[row["ownership"]],
        axis=1
)
scard_df["locale"] = scard_df.apply(lambda row: 
            locale_map[row["locale"]],
        axis=1
)

We can note that some rows do not have cost data associated with them, thus they are missing data.
Since we will use this cost data later in our analysis, we need to either interpolate the missing data
or drop the invalid rows. Here, we experiment with dropping rows with missing data.

In [50]:
scard_clipped = scard_df.dropna(subset=["net_cost", "in_state_tuition", "out_state_tuition"]).copy()
#print(scard_clipped["name"].unique().shape)
#print(scard_clipped.to_string())

It seems as if the clipped dataframe after dropping null cost data is just the data after 2009.
To verify that this is true, I try querying the original dataset purely by restricting the years.
If there is complete cost data from 2009 to 2020, then the resulting dataframe should be equal to the
dataframe resulting from dropping null data. Run the next code cell to confirm this.

In [51]:
scard_clipped_year = scard_df[scard_df["year"] >= 2009].copy()
scard_clipped_year.equals(scard_clipped)

True

In [52]:
msa_df["msa"] = msa_df["msa"].str.replace("]", "").astype(int)
msa_df

name  msa_income  msa_rent    msa  year
0             CO Metro Area"       59007      1207  19740  2009
1             NC Metro Area"       49902       921  20500  2009
2             FL Metro Area"       37654       881  23540  2009
3             NC Metro Area"       41272       789  24660  2009
4             SC Metro Area"       43283       763  24860  2009
..                       ...         ...       ...    ...   ...
56            CA Metro Area"       77774      1774  31080  2019
57            WI Metro Area"       75545      1218  31540  2019
58   DC-VA-MD-WV Metro Area"      105659      1862  47900  2019
59            NC Metro Area"       52322       815  49180  2019
60         MA-CT Metro Area"       76348      1319  49340  2019

[657 rows x 5 columns]

In [53]:
scard_clipped_geo = scard_clipped.dropna(subset=["cbsa", "puma"]).copy()
scard_clipped_geo

size  in_state_tuition  out_state_tuition      id  \
1989   6430.0           34973.0            34973.0  131159   
1990  19918.0            6972.0            19452.0  100858   
1991  19918.0            6972.0            19452.0  100858   
1992  12101.0           28070.0            28070.0  223232   
1993  11635.0            6761.0            14661.0  196079   
...       ...               ...                ...     ...   
3820   7366.0           57386.0            57386.0  179867   
3821   6217.0           23628.0            46854.0  231624   
3822   4804.0           54416.0            54416.0  168421   
3823   4701.0           57700.0            57700.0  130794   
3824   2619.0           46475.0            46475.0  197708   

                                   name  size_setting         zip  region_id  \
1989                American University            17  20016-8001          2   
1990                  Auburn University            15       36849          5   
1991                  Auburn University            15       36849          5   
1992                  Baylor University            16       76798          6   
1993              Binghamton University            16  13850-6000          2   
...                                 ...           ...         ...        ...   
3820  Washington University in St Louis            17  63130-4899          4   
3821                     William & Mary            14  23187-8795          5   
3822    Worcester Polytechnic Institute            13  01609-2280          1   
3823                    Yale University            17       06520          1   
3824                 Yeshiva University            14  10033-3299          2   

      state_fips           locale  ...  year  county     cbsa     puma  \
1989          11      City: Large  ...  2009     1.0  47900.0    101.0   
1990           1      City: Small  ...  2009    81.0  12220.0   2101.0   
1991           1      City: Small  ...  2009    81.0  10760.0   2101.0   
1992          48    City: Midsize  ...  2009   309.0  47380.0   3801.0   
1993          36  Suburb: Midsize  ...  2009     7.0  13780.0   2201.0   
...          ...              ...  ...   ...     ...      ...      ...   
3820          29    Suburb: Large  ...  2020   510.0  41180.0   2001.0   
3821          51    Suburb: Small  ...  2020   830.0  47260.0   9500.0   
3822          25    City: Midsize  ...  2020    27.0  49340.0    505.0   
3823           9    City: Midsize  ...  2020     9.0  35300.0  20601.0   
3824          36      City: Large  ...  2020    61.0  35620.0   4112.0   

      net_cost  net_cost_adjusted  in_tuition_adjusted  out_tuition_adjusted  \
1989   40345.0       18803.189093         16299.514987          16299.514987   
1990   13225.0        6163.642973          3249.370042           9065.798345   
1991   13225.0        6163.642973          3249.370042           9065.798345   
1992   24174.0       11266.533477         13082.303082          13082.303082   
1993   13999.0        6524.373382          3151.031391           6832.905076   
...        ...                ...                  ...                   ...   
3820   26921.0       10400.208357         22169.546331          22169.546331   
3821   19593.0        7569.231542          9128.045877          18100.789806   
3822   42835.0       16548.156642         21022.166263          21022.166263   
3823   15296.0        5909.200514         22290.851833          22290.851833   
3824   39536.0       15273.676223         17954.373292          17954.373292   

      non_tuition_expenses_adj       region  
1989               2503.674106     Mid East  
1990               2914.272931    Southeast  
1991               2914.272931    Southeast  
1992              -1815.769605    Southwest  
1993               3373.341992     Mid East  
...                        ...          ...  
3820             -11769.337974       Plains  
3821              -1558.814335    Southeast  
3822              -4474.009620  New Eng

In [54]:
scard_clipped_geo["puma"] = scard_clipped_geo["puma"].astype(int)
scard_clipped_geo["cbsa"] = scard_clipped_geo["cbsa"].astype(int)
print(scard_clipped_geo["puma"].unique().shape)
scard_clipped_geo

(111,)


size  in_state_tuition  out_state_tuition      id  \
1989   6430.0           34973.0            34973.0  131159   
1990  19918.0            6972.0            19452.0  100858   
1991  19918.0            6972.0            19452.0  100858   
1992  12101.0           28070.0            28070.0  223232   
1993  11635.0            6761.0            14661.0  196079   
...       ...               ...                ...     ...   
3820   7366.0           57386.0            57386.0  179867   
3821   6217.0           23628.0            46854.0  231624   
3822   4804.0           54416.0            54416.0  168421   
3823   4701.0           57700.0            57700.0  130794   
3824   2619.0           46475.0            46475.0  197708   

                                   name  size_setting         zip  region_id  \
1989                American University            17  20016-8001          2   
1990                  Auburn University            15       36849          5   
1991                  Auburn University            15       36849          5   
1992                  Baylor University            16       76798          6   
1993              Binghamton University            16  13850-6000          2   
...                                 ...           ...         ...        ...   
3820  Washington University in St Louis            17  63130-4899          4   
3821                     William & Mary            14  23187-8795          5   
3822    Worcester Polytechnic Institute            13  01609-2280          1   
3823                    Yale University            17       06520          1   
3824                 Yeshiva University            14  10033-3299          2   

      state_fips           locale  ...  year  county   cbsa   puma  net_cost  \
1989          11      City: Large  ...  2009     1.0  47900    101   40345.0   
1990           1      City: Small  ...  2009    81.0  12220   2101   13225.0   
1991           1      City: Small  ...  2009    81.0  10760   2101   13225.0   
1992          48    City: Midsize  ...  2009   309.0  47380   3801   24174.0   
1993          36  Suburb: Midsize  ...  2009     7.0  13780   2201   13999.0   
...          ...              ...  ...   ...     ...    ...    ...       ...   
3820          29    Suburb: Large  ...  2020   510.0  41180   2001   26921.0   
3821          51    Suburb: Small  ...  2020   830.0  47260   9500   19593.0   
3822          25    City: Midsize  ...  2020    27.0  49340    505   42835.0   
3823           9    City: Midsize  ...  2020     9.0  35300  20601   15296.0   
3824          36      City: Large  ...  2020    61.0  35620   4112   39536.0   

      net_cost_adjusted  in_tuition_adjusted  out_tuition_adjusted  \
1989       18803.189093         16299.514987          16299.514987   
1990        6163.642973          3249.370042           9065.798345   
1991        6163.642973          3249.370042           9065.798345   
1992       11266.533477         13082.303082          13082.303082   
1993        6524.373382          3151.031391           6832.905076   
...                 ...                  ...                   ...   
3820       10400.208357         22169.546331          22169.546331   
3821        7569.231542          9128.045877          18100.789806   
3822       16548.156642         21022.166263          21022.166263   
3823        5909.200514         22290.851833          22290.851833   
3824       15273.676223         17954.373292          17954.373292   

      non_tuition_expenses_adj       region  
1989               2503.674106     Mid East  
1990               2914.272931    Southeast  
1991               2914.272931    Southeast  
1992              -1815.769605    Southwest  
1993               3373.341992     Mid East  
...                        ...          ...  
3820             -11769.337974       Plains  
3821              -1558.814335    Southeast  
3822              -4474.009620  New England  
3823             -16381.651319  New Engla

In [55]:
scard_df = scard_clipped_geo
scard_df = pd.merge(scard_df, puma_df, left_on=["puma", "year"], right_on=["puma", "year"], how="inner")
scard_df["name"].unique().shape

(70,)

In [56]:
scard_df = pd.merge(scard_df, msa_df, left_on=["cbsa", "year"], right_on=["msa", "year"], how="left")
scard_df["name_y"].unique().shape

(33,)

<hr size=7 color=#8D84B5 > </hr> 

<div align="center">

## <font color = #6b4cde face="Verdana"> **Exploratory Analysis and Data Visualization** </font>
</center>

</div>

<hr size=7 color=#8D84B5 > </hr> 

In this section, we will be analyzing different components of our dataset graphically to display relationships present within it. For example, in this next block, we look at a violin plot of the net cost of every university and how it changes every year. Since the purpose of a violin plot is to visualize a distribute of data, we are able to see the increasing volatility in the net cost of university as time goes on. 

In [57]:
fig = go.Figure()
fig.add_trace(
    go.Violin(
        x=scard_df['year'], 
        y=scard_df['net_cost'],
        box_visible=True,
        meanline_visible=True
    )
)
fig.show()

We can observe that cost seems to be a bimodal distribution of cost, implying multple factors with significant variance.
Lets keep exploring the data and see if this holds for other costs.

In [58]:
fig = go.Figure()
fig.add_trace(
    go.Violin(
        x=scard_df['year'], 
        y=scard_df['in_state_tuition'],
        box_visible=True,
        meanline_visible=True
    )
)
fig.show()

In [59]:
fig = go.Figure()
fig.add_trace(
    go.Violin(
        x=scard_df['year'], 
        y=scard_df['out_state_tuition'],
        box_visible=True,
        meanline_visible=True
    )
)
fig.show()

It seems as if this binomial distribution exists for all of our cost data for tuition. Let's look at whether public or private institutions behave differently.

In [60]:
fig = px.scatter(scard_df, x="year", y="in_state_tuition", facet_col="ownership")
fig.show()


In [61]:
fig = px.scatter(scard_df, x="year", y="in_tuition_adjusted", facet_col="ownership")
fig.show()

In [62]:
fig = px.scatter(scard_df, x="year", y="out_tuition_adjusted", facet_col="ownership")
fig.show()

Aha! It seems as if we have determined that there is a relationship between public and private ownership and net costs, as they visibly vary differntly. We can explore this in our analysis later. Next, lets look at our census data. MSA groupings are major geographical items for the census, and can be useful to compare against smaller items.

In [63]:
fig = make_subplots(rows=1, cols=2)
fig.add_trace(
    go.Violin(x=msa_df["year"], 
              y=msa_df["msa_income"], 
              box_visible=True,
              meanline_visible=True
             ),
    row=1, col=1
)
fig.add_trace(
    go.Violin(x=msa_df["year"], 
              y=msa_df["msa_rent"], 
              box_visible=True,
              meanline_visible=True
             ),
    row=1, col=2
)

fig.update_xaxes(title_text="Year", row=1, col=1)
fig.update_xaxes(title_text="Year", row=1, col=2)
fig.update_yaxes(title_text="Median Household Income", row=1, col=1)
fig.update_yaxes(title_text="Median Monthly Rent ", row=1, col=2)
fig.update_layout(title_text="Household Income vs. Monthly Rent Over Time for MSA Adjusted for Inflation")
fig.show()

It seems as if rent and income across our MSA's are mostly normally distributed within years, and are varying with time. Let's do the same with PUMAs, smaller geographical items for the census and more representative of the immediate relevant area around our colleges.

In [64]:
fig = make_subplots(rows=1, cols=2)
fig.add_trace(
    go.Violin(x=puma_df["year"], 
              y=puma_df["puma_income"], 
              box_visible=True,
              meanline_visible=True
             ),
    row=1, col=1
)
fig.add_trace(
    go.Violin(x=puma_df["year"], 
              y=puma_df["puma_rent"], 
              box_visible=True,
              meanline_visible=True
             ),
    row=1, col=2
)

fig.update_xaxes(title_text="Year", row=1, col=1)
fig.update_xaxes(title_text="Year", row=1, col=2)
fig.update_yaxes(title_text="Median Household Income", row=1, col=1)
fig.update_yaxes(title_text="Median Monthly Rent", row=1, col=2)
fig.update_layout(title_text="Household Income vs. Monthly Rent Over Time for PUMA")
fig.show()

The same holds true for PUMAs! However, it's possible that inflation accounts for our yearly variance, lets normalize using an
all items CPI and try again.

In [65]:
msa_df["msa_income_adj"] = msa_df.apply(lambda row: 
            (row["msa_income"]/cpi_df.at[row["year"]]) * 100,
        axis=1
)
msa_df["msa_rent_adj"] = msa_df.apply(lambda row: 
            (row["msa_rent"]/cpi_df.at[row["year"]]) * 100,
        axis=1
)
scard_df["msa_income_adj"] = scard_df.apply(lambda row: 
            (row["msa_income"]/cpi_df.at[row["year"]]) * 100,
        axis=1
)
scard_df["msa_rent_adj"] = scard_df.apply(lambda row: 
            (row["msa_rent"]/cpi_df.at[row["year"]]) * 100,
        axis=1
)
scard_df["msa_rent_adj_ytd"] = scard_df.apply(lambda row: 
            (row["msa_rent"]/cpi_df.at[row["year"]]) * 100 * 12,
        axis=1
)


fig = make_subplots(rows=1, cols=2)
fig.add_trace(
    go.Violin(x=msa_df["year"], 
              y=msa_df["msa_income_adj"], 
              box_visible=True,
              meanline_visible=True
             ),
    row=1, col=1
)
fig.add_trace(
    go.Violin(x=msa_df["year"], 
              y=msa_df["msa_rent_adj"], 
              box_visible=True,
              meanline_visible=True
             ),
    row=1, col=2
)

fig.update_xaxes(title_text="Year", row=1, col=1)
fig.update_xaxes(title_text="Year", row=1, col=2)
fig.update_yaxes(title_text="Median Household Income", row=1, col=1)
fig.update_yaxes(title_text="Median Monthly Rent ", row=1, col=2)
fig.update_layout(title_text="Household Income vs. Monthly Rent Over Time for MSA Adjusted for Inflation")
fig.show()

In [66]:
puma_df["puma_income_adj"] = puma_df.apply(lambda row: 
            (row["puma_income"]/cpi_df.at[row["year"]]) * 100,
        axis=1
)
puma_df["puma_rent_adj"] = puma_df.apply(lambda row: 
            (row["puma_rent"]/cpi_df.at[row["year"]]) * 100,
        axis=1
)
scard_df["puma_income_adj"] = scard_df.apply(lambda row: 
            (row["puma_income"]/cpi_df.at[row["year"]]) * 100,
        axis=1
)
scard_df["puma_rent_adj"] = scard_df.apply(lambda row: 
            (row["puma_rent"]/cpi_df.at[row["year"]]) * 100,
        axis=1
)
scard_df["puma_rent_adj_ytd"] = scard_df.apply(lambda row: 
            (row["puma_rent"]/cpi_df.at[row["year"]]) * 100 * 12,
        axis=1
)

fig = make_subplots(rows=1, cols=2)
fig.add_trace(
    go.Violin(x=puma_df["year"], 
              y=puma_df["puma_income_adj"], 
              box_visible=True,
              meanline_visible=True
             ),
    row=1, col=1
)
fig.add_trace(
    go.Violin(x=puma_df["year"], 
              y=puma_df["puma_rent_adj"], 
              box_visible=True,
              meanline_visible=True
             ),
    row=1, col=2
)

fig.update_xaxes(title_text="Year", row=1, col=1)
fig.update_xaxes(title_text="Year", row=1, col=2)
fig.update_yaxes(title_text="Median Household Income", row=1, col=1)
fig.update_yaxes(title_text="Median Monthly Rent", row=1, col=2)
fig.update_layout(title_text="Household Income vs. Monthly Rent Over Time for PUMA Adjusted for Inflation")
fig.show()

There seems to be some fluctuation over time now, but it seems siginificantly less important now. What about the relationship between
rent and and nearby university costs? Let's plot the relevant data and break it down by ownership of nearby institutions to see if the areas around public and private institutions behave differently.

In [67]:
fig = px.scatter(scard_df, x="net_cost_adjusted", y="msa_rent_adj_ytd", trendline="ols", facet_col="ownership")
fig.show()

The trend lines are different, so it does seem that our relationship for ownership also seems to affect rent data as well. Lets see if our distribution of rents across our PUMAs is normal for public and private institutions.

In [68]:
fig = px.violin(scard_df, x="ownership", y="puma_rent_adj_ytd")
fig.show()

It seems as if there is some other factor flattening the distribution for PUMAs surrounding private institutions. Lets look at locality and the density of the surrounding area to see if there is a relationship there.

In [69]:
fig = px.violin(scard_df, x="locale", y="puma_rent_adj_ytd")
fig.show()

While rent across different localities are mostly monopolar, rural and remote towns are bimodal, and larger localities are slightly verically skewed.

<hr size=7 color=#8D84B5 > </hr> 

<div align="center">

## <font color = #6b4cde face="Verdana"> **Analysis, Hypothesis Testing, and Machine Learning** </font>
</center>

</div>

<hr size=7 color=#8D84B5 > </hr> 

Since monthly rent appears to increase linearly proportionately to household income, I will be using a Least Squares Linear Regression to highlight this relationship.

In [70]:
fig = px.scatter(msa_df, x="msa_rent_adj", y="msa_income_adj", trendline="ols")
fig.show()

In [71]:
results = px.get_trendline_results(fig)
print(results.px_fit_results.iloc[0].summary())

                            OLS Regression Results                            
Dep. Variable:                      y   R-squared:                       0.810
Model:                            OLS   Adj. R-squared:                  0.810
Method:                 Least Squares   F-statistic:                     2797.
Date:                Fri, 12 May 2023   Prob (F-statistic):          1.32e-238
Time:                        23:17:17   Log-Likelihood:                -6045.3
No. Observations:                 657   AIC:                         1.209e+04
Df Residuals:                     655   BIC:                         1.210e+04
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const       6634.8486    361.556     18.351      0.0

In [72]:
fig = px.scatter(puma_df, x="puma_rent_adj", y="puma_income_adj", trendline="ols")
fig.show()

In [73]:
results = px.get_trendline_results(fig)
print(results.px_fit_results.iloc[0].summary())

                            OLS Regression Results                            
Dep. Variable:                      y   R-squared:                       0.716
Model:                            OLS   Adj. R-squared:                  0.716
Method:                 Least Squares   F-statistic:                     8616.
Date:                Fri, 12 May 2023   Prob (F-statistic):               0.00
Time:                        23:17:18   Log-Likelihood:                -33340.
No. Observations:                3419   AIC:                         6.668e+04
Df Residuals:                    3417   BIC:                         6.670e+04
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const       5487.7969    211.505     25.946      0.0

As can be seen by the OLS Regression Summary, the MSA plot has a much more accurate regression with an R-squared of 0.814 compared to PUMA's 0.721, but this can be explained by PUMA having significantly more data points (PUMAs are more specific than MSAs) and the variance among the data is significantly wider (For example, the monthly rent for MSA does not even exceed 1000, but the montly rent for PUMA goes well above 1100). This, as well as many other factors, shows a strong tendency for universities to affect pricing much more on a small scale, such as a city level, than a county or metropolitan-center-wide scale.

### Multivariate Analysis

Lets try to combine the relationships we found between cost, ownership, and locality in our EDA into a model that describes
the relationship between our colleges and the Public Use Microdata Areas and MSAs surrounding them. To do this, we will make
multiple models that represent different possible relationships, and then fit those models to our data. This next cell will
generate and fit our models.

In [74]:
puma_rent_model = smf.ols(formula="puma_rent_adj ~ year * ownership + in_tuition_adjusted", data=scard_df)
puma_rent_res = puma_rent_model.fit()

msa_rent_model = smf.ols(formula="msa_rent_adj ~ year * ownership + in_tuition_adjusted", data=scard_df)
msa_rent_res = msa_rent_model.fit()

prm2 = smf.ols(formula="puma_rent_adj ~ year * ownership", data=scard_df)
prm2_res = prm2.fit()

prm3 = smf.ols(formula="puma_rent_adj ~ year * ownership + locale", data=scard_df)
prm3_res = prm3.fit()

num = len(scard_df["year"].values)
df_samples = scard_df[["year", "ownership", "in_tuition_adjusted"]]
df_samples = sm.add_constant(df_samples)
sample_set = np.column_stack(
    (
        np.ones(num), 
        scard_df["year"].values, 
        scard_df["ownership"].values,
        scard_df["in_tuition_adjusted"].values,
    )
)

df_samples2 = scard_df[["year", "ownership"]]
df_samples2 = sm.add_constant(df_samples)
sample_set2 = np.column_stack(
    (
        np.ones(num), 
        scard_df["year"].values, 
        scard_df["ownership"].values,
    )
)
scard_df["puma_rent_fit"] = puma_rent_res.predict(df_samples)
scard_df["puma_rent_fit2"] = prm2_res.predict(df_samples)
scard_df["msa_rent_fit"] = msa_rent_res.predict(df_samples)

Lets plot the first model we created, assuming a relationship between year, cost, and ownership in determining rents.

In [75]:
fig = make_subplots(rows=2, cols=1)

fig.update_layout(height=800, width=800, title_text="Interaction Model Public Use MicroData Area Rent Distribution and Trend Lines")
for i,id in enumerate (scard_df["ownership"].unique()):
    sub_df = scard_df[scard_df["ownership"] == id].copy().sort_values(by="year")

    trend_df = sub_df.groupby("year")["puma_rent_fit"].mean()
    fig.add_trace(
        go.Violin(
            x=sub_df['year'], 
            y=sub_df['puma_rent_adj'],
            name=id,
        ),
        row=(i+1), col=1
    )
    fig.add_trace(
        go.Scatter(
            x=trend_df.index, 
            y=trend_df,
            name=id,
        ),
        row=(i+1), col=1
    )
fig.show()

The variancy by years is negligible, but it seems as if the rents for public university communities are trending downwards, and private, upwards. Lets look at our MSA data as well to see if this is reflected in broader geographical regions.

In [76]:
fig = make_subplots(rows=2, cols=1)

fig.update_layout(height=800, width=800, title_text="Interaction Model Metropolitan Statistical Area Rent Distribution and Trend Lines")
for i,id in enumerate (scard_df["ownership"].unique()):
    sub_df = scard_df[scard_df["ownership"] == id].copy().sort_values(by="year")

    trend_df = sub_df.groupby("year")["msa_rent_fit"].mean()
    fig.add_trace(
        go.Violin(
            x=sub_df['year'], 
            y=sub_df['msa_rent_adj'],
            name=id,
        ),
        row=(i+1), col=1
    )
    fig.add_trace(
        go.Scatter(
            x=trend_df.index, 
            y=trend_df,
            name=id,
        ),
        row=(i+1), col=1
    )
fig.show()

Interestingly, the prior relationship is inverted, and the private data seems to be somewhat bimodal, implying we are missing a variable. From now on, lets analyze our OLS summaries and p values for significance.

In [77]:
print(puma_rent_res.summary())
print(puma_rent_res.pvalues)


                            OLS Regression Results                            
Dep. Variable:          puma_rent_adj   R-squared:                       0.003
Model:                            OLS   Adj. R-squared:                  0.002
Method:                 Least Squares   F-statistic:                     3.598
Date:                Fri, 12 May 2023   Prob (F-statistic):            0.00619
Time:                        23:17:18   Log-Likelihood:                -31199.
No. Observations:                4777   AIC:                         6.241e+04
Df Residuals:                    4772   BIC:                         6.244e+04
Df Model:                           4                                         
Covariance Type:            nonrobust                                         
                               coef    std err          t      P>|t|      [0.025      0.975]
--------------------------------------------------------------------------------------------
Intercept               

Our first model analyzing cost, years, and ownership has a good F statistic of 0.006, implying that the model that we have is significant,however, the pvalues of our variables individually do not reach the level of significance of p: < 0.05. Lets try a different model, this time without tuition costs.

In [78]:
print(prm2_res.summary())
print(prm2_res.pvalues)


                            OLS Regression Results                            
Dep. Variable:          puma_rent_adj   R-squared:                       0.003
Model:                            OLS   Adj. R-squared:                  0.002
Method:                 Least Squares   F-statistic:                     4.141
Date:                Fri, 12 May 2023   Prob (F-statistic):            0.00610
Time:                        23:17:18   Log-Likelihood:                -31200.
No. Observations:                4777   AIC:                         6.241e+04
Df Residuals:                    4773   BIC:                         6.243e+04
Df Model:                           3                                         
Covariance Type:            nonrobust                                         
                               coef    std err          t      P>|t|      [0.025      0.975]
--------------------------------------------------------------------------------------------
Intercept               

This model with only years and ownership provides a slightly better F statistic, thus is slightly more predictive, and its variable's p values are closer to 0.05, however, they still do not reach the level of clear statistical significance. This seems to be the right track though. Lets see what happens when incorporating locale into our model.

In [82]:
print(prm3_res.summary())

                            OLS Regression Results                            
Dep. Variable:          puma_rent_adj   R-squared:                       0.076
Model:                            OLS   Adj. R-squared:                  0.074
Method:                 Least Squares   F-statistic:                     43.48
Date:                Fri, 12 May 2023   Prob (F-statistic):           1.50e-75
Time:                        23:26:29   Log-Likelihood:                -31017.
No. Observations:                4777   AIC:                         6.205e+04
Df Residuals:                    4767   BIC:                         6.212e+04
Df Model:                           9                                         
Covariance Type:            nonrobust                                         
                                coef    std err          t      P>|t|      [0.025      0.975]
---------------------------------------------------------------------------------------------
Intercept             

In [81]:
print(prm3_res.pvalues)

Intercept                    4.716967e-01
ownership[T.Public]          4.350981e-02
locale[T.City: Midsize]      4.523786e-02
locale[T.City: Small]        1.154238e-35
locale[T.Rural: Fringe]      6.957702e-01
locale[T.Suburb: Large]      5.901630e-01
locale[T.Suburb: Midsize]    3.624453e-25
locale[T.Town: Remote]       1.913221e-38
year                         6.416813e-01
year:ownership[T.Public]     4.375242e-02
dtype: float64


As can be seen by the OLS Regression Summary, this model incorporating locale, ownership, and year has a much more accurate regression with a near zero F statistic, and with almost all of its variables crossing the threshold into statistical significance. This would suggest that the interaction between rents in the region surrounding a college, and the characteristics of that college and region, vary strongly based on the locality of the university, and the ownership of the college. This makes sense going by locality, as a university in a major city might increase rent, but will overall have a less drastic effect, wheras the significance of the city will also likely mean more universities will be hosted there, leading to a smaller coefficient. On the other hand, a university setting up shop in a small town would much more significantly increase the housing demand and value in the area, leading to a larger coefficient.

<hr size=7 color=#8D84B5 > </hr> 

<div align="center">

## <font color = #6b4cde face="Verdana"> **Insight and Policy Decision** </font>
</center>

</div>

<hr size=7 color=#8D84B5 > </hr> 

Based on our observations throughout our project, we can conclude:
1. There is a correlation between median income and median housing costs
2. As time continues, both median income and median housing costs will likely continue rising due to inflation.
3. Localities near universities are more volatile and are often significantly more expensive than the housing further out from them, creating a heavily gentrified environment (We can see an example of this in College Park)

If you would like to learn more about the tools we used to make this:
* [Census API](https://www.census.gov/data/developers/guidance/api-user-guide.Overview.html#list-tab-2080675447)
* [Andrew G. Reiter, “U.S. News & World Report Historical Liberal Arts College and University Rankings,” available at: http://andyreiter.com/datasets/](https://andyreiter.com/datasets/) 
* [College Scorecard API](https://collegescorecard.ed.gov/data/documentation/)
* [Zip To Tract API/Excel Doc](https://www.huduser.gov/portal/datasets/usps_crosswalk.html#data)
* [Department of Labor Beta Labs Historical CPI Data](https://beta.bls.gov/dataViewer/view/timeseries/CUSR0000SA0;jsessionid=7A226A5ECD1A6315D201A5164D28574A)